In [1]:
import numpy as np
import scipy.sparse as sps
import porepy as pp

In [2]:
import sys
sys.path.append("./class")
from Transport_class import Transport
from Reaction_class import Reaction
from Concentrations import Concentrations

In [3]:
#QUESTIONE DATI
Nx=100
Nt=10000
L=0.045
h=L/Nx
phys_dims=[L]
g=pp.CartGrid([Nx],phys_dims)
g.compute_geometry()
#pp.plot_grid(g,figsize=(15,12))
#pp.plot_grid(g)

In [4]:
psi1=np.zeros(Nx)
psi2=np.zeros(Nx)
psi3=np.zeros(Nx)
psi4=np.zeros(Nx)
psi5=np.zeros(Nx)
psi6=np.zeros(Nx)
rd=np.zeros(Nx)

In [5]:
unity = np.ones(g.num_cells)
porosity=0.3*unity
aperture=1

In [6]:
reaction_data={#"kd":1.83e-7,
               "kd":0.0,
               "K_eq":4.45e-7,
               "K_sol":10e9,
               "porosity":porosity }

In [7]:
reaction=Reaction(g,reaction_data)

In [8]:
K_eq=reaction.data[pp.PARAMETERS]["reaction"]["K_eq"]

In [9]:
bc_type_Ca=["dir","dir"]
bc_value_Ca=[0.0,0.0]
#init_cond_Ca=lambda x,y,z:int(x<0.5)
init_cond_Ca=lambda x,y,z:0.0

bc_type_CaSiO3=["dir","dir"]
bc_value_CaSiO3=[0.0,0.0]
#init_cond_CaSiO3=lambda x,y,z:int(x<0.5)
init_cond_CaSiO3=lambda x,y,z:1.0

bc_type_CO2=["dir","dir"]
bc_value_CO2=[0.3691108,0.0]
#init_cond_Ca=lambda x,y,z:int(x<0.5)
init_cond_CO2=lambda x,y,z:1.0e-3

bc_type_SiO2=["dir","dir"]
bc_value_SiO2=[0.0,0.0]
#init_cond_Ca=lambda x,y,z:int(x<0.5)
init_cond_SiO2=lambda x,y,z:0.0

bc_type_H_piu=["dir","dir"]
bc_value_H_piu=[1.0e-5,0.0]
#init_cond_Ca=lambda x,y,z:int(x<0.5)
init_cond_H_piu=lambda x,y,z:1.0e-7



bc_HCO3_in=K_eq*bc_value_CO2[0]/bc_value_H_piu[0]
print("bc_HCO3_in=")
print(bc_HCO3_in)
#bc_HCO3_out=K_eq*bc_value_CO2[1]/bc_value_H_piu[1]
bc_HCO3_out=0.0

bc_type_HCO3=["dir","dir"]
bc_value_HCO3=[bc_HCO3_in,bc_HCO3_out]
#init_cond_Ca=lambda x,y,z:int(x<0.5)
init_cond_HCO3=lambda x,y,z:0.0

bc_HCO3_in=
0.0164254306


In [10]:
data_6reagents = {"bc_type_Ca": bc_type_Ca,
            "bc_value_Ca": bc_value_Ca,
            "bc_type_CO2": bc_type_CO2,
            "bc_value_CO2": bc_value_CO2,
            "bc_type_HCO3": bc_type_HCO3,
            "bc_value_HCO3": bc_value_HCO3,
            "bc_type_CaSiO3": bc_type_CaSiO3,
            "bc_value_CaSiO3": bc_value_CaSiO3,
            "bc_type_SiO2": bc_type_SiO2,
            "bc_value_SiO2": bc_value_SiO2,
            "bc_type_H_piu": bc_type_H_piu,
            "bc_value_H_piu": bc_value_H_piu,
            "time_step": 34.56,
            "t_max": 345600,
            "method": "Implicit",
            "lambda_lin_decay":0,
            "init_cond_Ca":init_cond_Ca,
            "init_cond_CO2":init_cond_CO2,
            "init_cond_CaSiO3":init_cond_CaSiO3,
            "init_cond_SiO2":init_cond_SiO2,
            "init_cond_HCO3":init_cond_HCO3,
            "init_cond_H_piu":init_cond_H_piu,}

In [11]:
concentrations=Concentrations(g,Nt,data_6reagents)
concentrations.set_initial_cond(K_eq)

In [12]:
psi1,psi2,psi3,psi4,psi5=concentrations.compute_psi(0,psi1,psi2,psi3,psi4,psi5)

In [13]:
bc_psi1,bc_psi2,bc_psi3,bc_psi4,bc_psi5=concentrations.set_bc_psi()

In [14]:
print(bc_psi5)

[0.0, 0.0]


In [15]:
data_reagent_psi1= {
            "bc_type": bc_type_Ca,
            "bc_value": bc_psi1,
            "mass_weight": porosity * aperture,
            "darcy_flux":6.67e-9*np.ones(g.num_faces),
            "lambda_lin_decay":0.,
            "method": "Implicit",
            "time_step": 34.56,
            "t_max": 345600,
}

data_reagent_psi2= {
            "bc_type": bc_type_H_piu,
            "bc_value": bc_psi2,
            "mass_weight": porosity * aperture,
            "darcy_flux":6.67e-9*np.ones(g.num_faces),
            "lambda_lin_decay":0.,
            "method": "Implicit",
            "time_step": 34.56,
            "t_max": 345600,
}

data_reagent_psi3= {
            "bc_type": bc_type_CO2,
            "bc_value": bc_psi3,
            "mass_weight": porosity * aperture,
            "darcy_flux":6.67e-9*np.ones(g.num_faces),
            "lambda_lin_decay":0.,
            "method": "Implicit",
            "time_step": 34.56,
            "t_max": 345600,
}

data_reagent_psi4= {
            "bc_type": bc_type_CaSiO3,
            "bc_value": bc_psi4,
            "mass_weight": porosity * aperture,
            "darcy_flux":np.zeros(g.num_faces),
            "lambda_lin_decay":0.,
            "method": "Implicit",
            "time_step": 34.56,
            "t_max": 345600,
}

data_reagent_psi5= {
            "bc_type": bc_type_SiO2,
            "bc_value": bc_psi5,
            "mass_weight": porosity * aperture,
            "darcy_flux":6.67e-9*np.ones(g.num_faces),
            "lambda_lin_decay":0.,
            "method": "Implicit",
            "time_step": 34.56,
            "t_max": 345600,
}

In [17]:
psi1_transport=Transport(g,data_reagent_psi1)
#psi1=psi1_transport.set_bc(psi1)
psi1_transport.set_bc()
psi1_lhs,psi1_rhs_b,psi1_rhs_matrix=psi1_transport.get_transport_lhs_rhs()

psi2_transport=Transport(g,data_reagent_psi2)
#psi2=psi2_transport.set_bc(psi2)
psi2_transport.set_bc()
psi2_lhs,psi2_rhs_b,psi2_rhs_matrix=psi2_transport.get_transport_lhs_rhs()
#print("psi2_lhs=")
#print(psi2_lhs)
#print("psi2_rhs_b=")
#print(psi2_rhs_b)
#print("psi2_rhs_matrix")
#print(psi2_rhs_matrix)

psi3_transport=Transport(g,data_reagent_psi3)
#psi3=psi3_transport.set_bc(psi3)
psi3_transport.set_bc()
psi3_lhs,psi3_rhs_b,psi3_rhs_matrix=psi3_transport.get_transport_lhs_rhs()
#print("psi3_lhs=")
#print(psi3_lhs)
#print("psi3_rhs_b=")
#print(psi3_rhs_b)
#print("psi3_rhs_matrix")
#print(psi3_rhs_matrix)

psi4_transport=Transport(g,data_reagent_psi4)
#psi4=psi4_transport.set_bc(psi4)
psi4_transport.set_bc()
psi4_lhs,psi4_rhs_b,psi4_rhs_matrix=psi4_transport.get_transport_lhs_rhs()
#print("psi4_lhs=")
#print(psi4_lhs)
#print("psi4_rhs_b=")
#print(psi4_rhs_b)
#print("psi4_rhs_matrix")
#print(psi4_rhs_matrix)

psi5_transport=Transport(g,data_reagent_psi5)
#psi5=psi5_transport.set_bc(psi5)
psi5_transport.set_bc()
psi5_lhs,psi5_rhs_b,psi5_rhs_matrix=psi5_transport.get_transport_lhs_rhs()
print("psi5_lhs=")
print(psi5_lhs)
print("psi5_rhs_b=")
print(psi5_rhs_b)
print("psi5_rhs_matrix")
print(psi5_rhs_matrix)

psi2_lhs=
  (0, 0)	3.912919999999999e-06
  (1, 0)	-6.67e-09
  (1, 1)	3.912919999999999e-06
  (2, 1)	-6.67e-09
  (2, 2)	3.91292e-06
  (3, 2)	-6.67e-09
  (3, 3)	3.912919999999998e-06
  (4, 3)	-6.67e-09
  (4, 4)	3.912919999999998e-06
  (5, 4)	-6.67e-09
  (5, 5)	3.912920000000002e-06
  (6, 5)	-6.67e-09
  (6, 6)	3.912919999999998e-06
  (7, 6)	-6.67e-09
  (7, 7)	3.912919999999998e-06
  (8, 7)	-6.67e-09
  (8, 8)	3.912919999999998e-06
  (9, 8)	-6.67e-09
  (9, 9)	3.912919999999998e-06
  (10, 9)	-6.67e-09
  (10, 10)	3.912919999999998e-06
  (11, 10)	-6.67e-09
  (11, 11)	3.912920000000006e-06
  (12, 11)	-6.67e-09
  (12, 12)	3.912919999999998e-06
  :	:
  (87, 87)	3.912919999999991e-06
  (88, 87)	-6.67e-09
  (88, 88)	3.912920000000052e-06
  (89, 88)	-6.67e-09
  (89, 89)	3.912919999999991e-06
  (90, 89)	-6.67e-09
  (90, 90)	3.912919999999991e-06
  (91, 90)	-6.67e-09
  (91, 91)	3.912919999999991e-06
  (92, 91)	-6.67e-09
  (92, 92)	3.912919999999991e-06
  (93, 92)	-6.67e-09
  (93, 93)	3.912919999999991

In [18]:
n_steps = int(np.round(concentrations.data[pp.PARAMETERS]["6reagents"]["t_max"] / concentrations.data[pp.PARAMETERS]["6reagents"]["time_step"]))

In [19]:
dt=psi1_transport.data[pp.PARAMETERS]["transport"]["time_step"]

In [20]:
save_every=100
exporter = pp.Exporter(g, file_name="6_reagents",folder_name="solution_6_reagents")

In [21]:
for i in range(1,n_steps+1,1):
#for i in range(1,5,1):
    if np.isclose((i-1) % save_every, 0):
        exporter.write_vtu({"Ca":concentrations.Ca[:,i-1], "CaSiO3":concentrations.CaSiO3[:,i-1], "H_piu":concentrations.H_piu[:,i-1], "HCO3":concentrations.HCO3[:,i-1], "CO2":concentrations.CO2[:,i-1],"SiO2":concentrations.SiO2[:,i-1]}, time_step=int((i-1) // save_every))

    psi1,psi2,psi3,psi4,psi5=concentrations.compute_psi(i-1,psi1,psi2,psi3,psi4,psi5)
    print("i=")
    print(i)
    print("psi1=")
    print(psi1)
    print("psi2=")
    print(psi2)
    print("psi3=")
    print(psi3)
    print("psi4=")
    print(psi4)
    print("psi5=")
    print(psi5)
    rd=reaction.compute_rd_6_reagents(concentrations.Ca[:,i-1],concentrations.SiO2[:,i-1],concentrations.H_piu[:,i-1],concentrations.CaSiO3[:,i-1],rd)
    print("rd=")
    print(rd)
    psi1,psi2,psi3,psi4,psi5=concentrations.one_step_transport_reaction(psi1,psi2,psi3,psi4,psi5,
                                               psi1_lhs,psi1_rhs_b,psi1_rhs_matrix,
                                               psi2_lhs,psi2_rhs_b,psi2_rhs_matrix,
                                               psi3_lhs,psi3_rhs_b,psi3_rhs_matrix,
                                               psi4_lhs,psi4_rhs_b,psi4_rhs_matrix,
                                               psi5_lhs,psi5_rhs_b,psi5_rhs_matrix,
                                               rd,h)
    
    concentrations.compute_concentration(psi1,psi2,psi3,psi4,psi5,i,K_eq)



exporter.write_vtu({"Ca":concentrations.Ca[:,-1], "CaSiO3":concentrations.CaSiO3[:,-1], "H_piu":concentrations.H_piu[:,-1], "HCO3":concentrations.HCO3[:,-1], "CO2":concentrations.CO2[:,-1],"SiO2":concentrations.SiO2[:,-1]}, time_step=(n_steps // save_every))
time_steps = np.arange(
    0, psi1_transport.data[pp.PARAMETERS]["transport"]["t_max"] + dt, save_every * dt
)
exporter.write_pvd(time_steps)
    

i=
1
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499 -0.0044499
 -0.004

rd=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
i=
4
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.00451099 -0.00445011 -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.004

/home/dell/.local/lib/python3.8/site-packages/scipy/sparse/linalg/dsolve/linsolve.py:318: SparseEfficiencyWarning: splu requires CSC matrix format
  warn('splu requires CSC matrix format', SparseEfficiencyWarning)


i=
6
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.00455154 -0.00445042 -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0

i=
9
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.0046121  -0.00445114 -0.00444991 -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0

...

i=
1276
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.01505636 -0.0121026  -0.00889026 -0.0065594  -0.00528996 -0.00473643
 -0.00453514 -0.00447235 -0.0044552  -0.00445103 -0.00445012 -0.00444994
 -0.00444991 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499 

i=
1282
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.0150702  -0.01213276 -0.00892315 -0.00658333 -0.00530303 -0.00474215
 -0.00453723 -0.00447301 -0.00445538 -0.00445108 -0.00445013 -0.00444994
 -0.00444991 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499 

i=
1288
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.0150839  -0.01216276 -0.00895602 -0.00660736 -0.00531621 -0.00474794
 -0.00453935 -0.00447367 -0.00445556 -0.00445112 -0.00445014 -0.00444994
 -0.00444991 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499 

i=
1294
psi1=
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0.]
psi2=
[-0.01509746 -0.01219259 -0.00898885 -0.00663147 -0.0053295  -0.00475381
 -0.00454151 -0.00447435 -0.00445575 -0.00445117 -0.00445015 -0.00444995
 -0.00444991 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499  -0.0044499
 -0.0044499  -0.0044499 

KeyboardInterrupt: 

In [ ]:
print("Ca=")
print(concentrations.Ca[:,2])
print("CaSiO3=")
print(concentrations.CaSiO3[:,2])
print("CO2=")
print(concentrations.CO2[:,2])
print("HCO3=")
print(concentrations.HCO3[:,2])
print("SiO2=")
print(concentrations.SiO2[:,2])
print("H_piu=")
print(concentrations.H_piu[:,2])

In [ ]:
exporter.write_pvd(time_steps)